In [1]:
import sys, fitz
from tqdm import tqdm

import datetime
import os

In [2]:
def bbox_overlap(bbox1, bbox2):
    # bbox1 和 bbox2 分别为两个边界框的坐标 [x1, y1, x2, y2]
    x1_1, y1_1, x2_1, y2_1 = bbox1
    x1_2, y1_2, x2_2, y2_2 = bbox2

    # 判断两个边界框是否有水平和垂直方向上的重叠
    if x1_1 <= x2_2 and x2_1 >= x1_2 and y1_1 <= y2_2 and y2_1 >= y1_2:
        return True
    else:
        return False

def replace_text(text):
    # 去除每个子列表中的换行符  
    for sublist in text:  
        for i in range(len(sublist)):  
            if isinstance(sublist[i], str):  
                sublist[i] = sublist[i].replace('\n', '')  
    return text

def table_to_markdown(table):
    markdown = "|"
    for header in table[0]:
        markdown += " " + str(header) + " |"
    markdown += "\n|"
    for _ in range(len(table[0])):
        markdown += " --- |"
    markdown += "\n"
    for row in table[1:]:
        markdown += "|"
        for item in row:
            markdown += " " + str(item) + " |"
        markdown += "\n"
    return markdown

In [3]:
def get_page_info(doc, page_number):
	page = doc.load_page(page_number)
	lines_width = []
	x0_list = []
	text_list = []
	font_size_list = []
	doc_dict = page.get_text("dict", sort=True)
	
	width = doc_dict["width"]
	height = doc_dict["height"]
	doc_blocks = doc_dict["blocks"]
	
	page_info = []
	images_bbox = []
	tables_bbox = []
	tables_record = []
	try:
		doc_tabs = page.find_tables()
		tabs_count = len(doc_tabs.tables)
	except Exception as e:
		tabs_count = 0
	if tabs_count > 0:
		for i, table in enumerate(doc_tabs):
			tables_bbox.append({"number": i, "bbox": table.bbox, "text": replace_text(table.extract())})
	images_list = page.get_image_info()
	if len(images_list) > 0:
		for image in images_list:
			image_bbox = image.get("bbox")
			
			if image_bbox:
				image_wide = image_bbox[2] - image_bbox[0]
				image_height = image_bbox[3] - image_bbox[1]
				if abs(image_wide - width) > 10 and abs(image_height - height) > 10:
					images_bbox.append(image_bbox)
	
	for i in range(len(doc_blocks)):
		doc_block = doc_blocks[i]
		block_type = doc_block["type"]
		block_bbox = doc_block["bbox"]
		is_overlap_table = False
		is_overlap_image = False
		if tabs_count > 0:
			for tab in tables_bbox:
				tab_number = tab["number"]
				tab_bbox = tab["bbox"]
				tab_info = tab["text"]
				is_overlap_table = bbox_overlap(tab_bbox, block_bbox)
				if is_overlap_table:
					if tab_number not in tables_record:
						tables_record.append(tab_number)
						page_info.append(
							{"page_number": page_number + 1, "type": 2, "number": tab_number, "bbox": tab_bbox,
							 "text": tab_info})
					break
		if len(images_bbox) >= 1:
			for image_bbox in images_bbox:
				is_overlap_image = bbox_overlap(image_bbox, block_bbox)
				if is_overlap_image:
					if block_type == 1:
						page_info.append({"page_number": page_number + 1, "type": 1, "bbox": image_bbox})
					break
		if is_overlap_image or is_overlap_table:
			continue
		if block_type == 0:
			block_lines = doc_block["lines"]
			origin_y = 0
			for j in range(len(block_lines)):
				block_line = block_lines[j]
				line_spans = block_line["spans"]
				line_bbox = block_line["bbox"]
				y0 = round(line_bbox[1], 2)
				line_width = round(int(line_bbox[2]) - int(line_bbox[0]), 2)
				x0 = int(line_bbox[0])
				x0_list.append(x0)
				lines_width.append(line_width)
				line_text = ""
				line_dict = {"size": 0, "font": [], "line_width": line_width, "bbox": line_bbox, "text": ""}
				line_size = 0
				for k in range(len(line_spans)):
					line_span = line_spans[k]
					span_size = round(line_span["size"], 2)
					if span_size > line_size:
						line_size = span_size
					span_text = line_span["text"]
					line_text = line_text + span_text
				line_dict["size"] = line_size
				line_dict["text"] = line_text
				font_size_list.append(line_size)
				if y0 - origin_y > 1:
					page_info.append({"page_number": page_number + 1, "type": 0, "line_width": line_width, "x0": x0,
					                  "line_size": line_size, "text": line_text})
					text_list.append(line_text)
				else:
					if j >= 1:
						page_info[-1]["text"] = page_info[-1]["text"] + "\t" + line_dict["text"]
						page_info[-1]["line_width"] = page_info[-1]["line_width"] + line_width
						text_list[-1] = page_info[-1]["text"]
	return page_info, lines_width, x0_list, text_list, font_size_list

In [4]:
file = r'pdf\韵达股份 2020年年度报告-2021-04-30.pdf'
doc = fitz.open(file)

total_pages = doc.page_count
pdf_info = []
x0_list = []
lines_width = []
text_list = []
font_size_list = []

for i in tqdm(range(total_pages)):
    page_info, l_width, x0, texts, fone_size = get_page_info(doc, i)
    lines_width += l_width
    x0_list += x0
    text_list += texts
    font_size_list += fone_size
    if len(page_info) >= 1:
        pdf_info.append(page_info)

print("有效总页数：", len(pdf_info))

100%|██████████| 318/318 [00:25<00:00, 12.50it/s]

有效总页数： 318


In [5]:
pdf_info

[[{'page_number': 1,
   'type': 0,
   'line_width': 177,
   'x0': 363,
   'line_size': 9.0,
   'text': '韵达控股股份有限公司 2020 年年度报告全文 '},
  {'page_number': 1,
   'type': 0,
   'line_width': 185,
   'x0': 207,
   'line_size': 18.0,
   'text': '韵达控股股份有限公司 '},
  {'page_number': 1,
   'type': 0,
   'line_width': 120,
   'x0': 239,
   'line_size': 15.96,
   'text': '2020 年年度报告 '},
  {'page_number': 1,
   'type': 0,
   'line_width': 96,
   'x0': 251,
   'line_size': 15.96,
   'text': '2021 年 04 月 '},
  {'page_number': 1,
   'type': 0,
   'line_width': 6,
   'x0': 534,
   'line_size': 9.0,
   'text': '1 '}],
 [{'page_number': 2,
   'type': 0,
   'line_width': 177,
   'x0': 363,
   'line_size': 9.0,
   'text': '韵达控股股份有限公司 2020 年年度报告全文 '},
  {'page_number': 2,
   'type': 0,
   'line_width': 221,
   'x0': 189,
   'line_size': 15.96,
   'text': '第一节 重要提示、目录和释义 '},
  {'page_number': 2,
   'type': 0,
   'line_width': 454,
   'x0': 84,
   'line_size': 14.04,
   'text': '公司董事会、监事会及董事、监事、高级管理人员保证年度报告内容的真'},

In [6]:
from collections import Counter
def get_constant(lines_width, x0_list, font_size_list, text_list, page_info):
	line_width_mode = Counter(lines_width).most_common(1)[0][0]
	x0_mode = Counter(x0_list).most_common(1)[0][0]
	font_size_cunt = Counter(font_size_list)
	text_list_count = Counter(text_list)
	duplicate_rows = []
	for i, j in text_list_count.items():
		if j >= len(page_info)*0.9:
			duplicate_rows.append(i)
	
	effective_font_size = []
	for i, j in font_size_cunt.items():
		if j >= 1:
			effective_font_size.append(i)
	font_size_mode = font_size_cunt.most_common(1)[0][0]
	print(f"""
	line width : {line_width_mode}
	x0 : {x0_mode}
	font size : {font_size_mode}
	duplicate rows : {duplicate_rows}
	effective font size : {effective_font_size}
	""")
	
	return line_width_mode, x0_mode, font_size_mode, duplicate_rows, effective_font_size

In [7]:
line_width_mode, x0_mode, font_size_mode, duplicate_rows, effective_font_size = get_constant(lines_width, x0_list,
	                                                                                             font_size_list,
	                                                                                             text_list, pdf_info)


	line width : 482
	x0 : 56
	font size : 9.0
	duplicate rows : ['韵达控股股份有限公司 2020 年年度报告全文 ']
	effective font size : [9.0, 18.0, 15.96, 14.04, 12.0, 10.56, 11.04, 15.0, 9.96]
	


In [8]:
def get_line_type(pdf_info, line_width_mode, x0_mode, font_size_mode, duplicate_rows, effective_font_size):
	new_pdf_info1 = []
	directory_text = ""
	directory_page_number = 0
	directory_flag = False
	directory_line_width = []
	for i, page_info in enumerate(pdf_info):
		page_text1 = []
		for j, line_info in enumerate(page_info):
			line_type = line_info["type"]
			page_number = line_info["page_number"]
			if line_type == 0:
				line_text = line_info["text"]
				line_width = line_info["line_width"]
				line_size = line_info["line_size"]
				line_x0 = line_info["x0"]
				line_description = ""
				line_text_flag = -1
				if directory_flag and page_number == directory_page_number:
					if line_width > 1.5 * line_size:
						if line_width not in directory_line_width :
							directory_line_width.append(line_width)
						
						line_description = "directory"
						directory_text += "\n" + line_text
						page_text1.append({"page_number": page_number, "text": line_text, "type": line_description,
										"text_flag": line_text_flag})
						continue
				
				elif directory_flag and page_number <= directory_page_number + 2:
					if line_width in directory_line_width:
						directory_text += "\n" + line_text
						line_description = "directory"
						page_text1.append({"page_number": page_number, "text": line_text, "type": line_description,
						                   "text_flag": line_text_flag})
						continue
					else:
						directory_flag = False
				else:
					directory_flag = False
				
				if line_text in duplicate_rows or line_size not in effective_font_size:
					continue
				elif line_text.replace(" ","")=="目录" :
					directory_flag = True
					directory_text += line_text
					directory_page_number = page_number
					line_description = "directory"
				elif abs(line_x0 - x0_mode) == 0:
					if abs(line_width - line_width_mode) <= line_size * 3:
						line_description = "text"
						line_text_flag = 2
					elif line_text in directory_text:
						line_description = "title"
					elif "." in line_text and "。" not in line_text and "；" not in line_text:
						line_description = "title"
					elif "。" in line_text or "；" in line_text or "：" in line_text:
						line_description = "text"
						line_text_flag = 3
					else:
						line_description = "text"
						line_text_flag = 3
				elif 0 < abs(line_x0 - x0_mode) <= line_size * 3:
					if abs(line_width - line_width_mode) <= line_size * 3:
						line_description = "text"
						line_text_flag = 1
					elif "。" in line_text or "？" in line_text or "；" in line_text:
						line_description = "text"
						line_text_flag = 1
					else:
						line_description = "title"
				elif abs(line_x0 - x0_mode) >= line_size * 3 and line_width > 2 * line_size:
					if "图" in line_text:
						line_description = "image name"
					elif "表" in line_text:
						line_description = "table name"
					else:
						line_description = "clutter"
				else:
					if line_width < 2 * line_size:
						continue
					else:
						line_description = "clutter"
				if line_description == "":
					print(line_info)
				page_text1.append({"page_number": page_number, "text": line_text, "type": line_description,
				                   "text_flag": line_text_flag})
			elif line_type == 1:
				page_text1.append({"page_number": page_number, "text": "", "type": "image", "text_flag": -1})
			elif line_type == 2:
				if len(page_text1) == 0:
					line_text_flag = 2
				else:
					line_text_flag = 1
				page_text1.append({"page_number": page_number, "text": line_info["text"], "type": "table",
				                   "text_flag": line_text_flag})
		new_pdf_info1 += page_text1
	return new_pdf_info1


In [9]:
new_pdf_info1 = get_line_type(pdf_info, line_width_mode, x0_mode, font_size_mode, duplicate_rows,
                                effective_font_size, )

In [10]:
new_pdf_info1

[{'page_number': 1, 'text': '韵达控股股份有限公司 ', 'type': 'clutter', 'text_flag': -1},
 {'page_number': 1, 'text': '2020 年年度报告 ', 'type': 'clutter', 'text_flag': -1},
 {'page_number': 1,
  'text': '2021 年 04 月 ',
  'type': 'clutter',
  'text_flag': -1},
 {'page_number': 2,
  'text': '第一节 重要提示、目录和释义 ',
  'type': 'clutter',
  'text_flag': -1},
 {'page_number': 2,
  'text': '公司董事会、监事会及董事、监事、高级管理人员保证年度报告内容的真',
  'type': 'text',
  'text_flag': 1},
 {'page_number': 2,
  'text': '实、准确、完整，不存在虚假记载、误导性陈述或重大遗漏，并承担个别和连',
  'type': 'text',
  'text_flag': 2},
 {'page_number': 2, 'text': '带的法律责任。 ', 'type': 'text', 'text_flag': 3},
 {'page_number': 2,
  'text': '公司负责人聂腾云、主管会计工作负责人谢万涛及会计机构负责人(会计主',
  'type': 'text',
  'text_flag': 1},
 {'page_number': 2,
  'text': '管人员)刘辉声明：保证本年度报告中财务报告的真实、准确、完整。 ',
  'type': 'text',
  'text_flag': 3},
 {'page_number': 2,
  'text': '所有董事均已出席了审议本报告的董事会会议。 ',
  'type': 'text',
  'text_flag': 1},
 {'page_number': 2,
  'text': '本报告中涉及的未来发展规划及经营目标相关的前瞻性陈述，属于计划性',
  'type': 'text'

In [11]:
def check_table_image(new_pdf_info1):
	new_pdf_info2 = []
	for i, line_info in enumerate(new_pdf_info1):
		page_number = line_info["page_number"]
		line_text = line_info["text"]
		if line_info["type"] == "table":
			if line_info["text_flag"] == 1:
				if new_pdf_info1[i - 1]["type"] not in ["table name", "table", "image"]:
					new_pdf_info2[-1]["type"] = "table name"
				
				new_pdf_info2.append(line_info)
			elif line_info["text_flag"] == 2:
				j = 1
				while j < len(new_pdf_info2):
					if new_pdf_info2[-j]["type"] == "table":
						if line_text[0] == new_pdf_info2[-j]["text"][0]:
							new_pdf_info2[-j]["text"] += line_text[1:]
						else:
							new_pdf_info2[-j]["text"] += line_text[:]
						break
					elif new_pdf_info2[-j]["type"] == "table name":
						previous_page_number = new_pdf_info2[-j]["page_number"]
						line_info["page_number"] = previous_page_number
						if j == 1:
							new_pdf_info2.append(line_info)
						else:
							new_pdf_info2.insert(-j + 1, line_info)
						break
					else:
						j += 1
		elif line_info["type"] == "image":
			if i < len(new_pdf_info1) - 1:
				if new_pdf_info1[i + 1]["type"] not in ["image name", "image", "table", "table name"] and \
						new_pdf_info1[i + 1]["page_number"] == page_number:
					new_pdf_info1[i + 1]["type"] = "image name"
		else:
			new_pdf_info2.append(line_info)
	return new_pdf_info2

In [12]:
new_pdf_info2 = check_table_image(new_pdf_info1)

In [13]:
new_pdf_info2

[{'page_number': 1, 'text': '韵达控股股份有限公司 ', 'type': 'clutter', 'text_flag': -1},
 {'page_number': 1, 'text': '2020 年年度报告 ', 'type': 'clutter', 'text_flag': -1},
 {'page_number': 1,
  'text': '2021 年 04 月 ',
  'type': 'clutter',
  'text_flag': -1},
 {'page_number': 2,
  'text': '第一节 重要提示、目录和释义 ',
  'type': 'clutter',
  'text_flag': -1},
 {'page_number': 2,
  'text': '公司董事会、监事会及董事、监事、高级管理人员保证年度报告内容的真',
  'type': 'text',
  'text_flag': 1},
 {'page_number': 2,
  'text': '实、准确、完整，不存在虚假记载、误导性陈述或重大遗漏，并承担个别和连',
  'type': 'text',
  'text_flag': 2},
 {'page_number': 2, 'text': '带的法律责任。 ', 'type': 'text', 'text_flag': 3},
 {'page_number': 2,
  'text': '公司负责人聂腾云、主管会计工作负责人谢万涛及会计机构负责人(会计主',
  'type': 'text',
  'text_flag': 1},
 {'page_number': 2,
  'text': '管人员)刘辉声明：保证本年度报告中财务报告的真实、准确、完整。 ',
  'type': 'text',
  'text_flag': 3},
 {'page_number': 2,
  'text': '所有董事均已出席了审议本报告的董事会会议。 ',
  'type': 'text',
  'text_flag': 1},
 {'page_number': 2,
  'text': '本报告中涉及的未来发展规划及经营目标相关的前瞻性陈述，属于计划性',
  'type': 'text'

In [15]:
def get_page_info_dict(new_pdf_info2):
	page_info_dict = {}
	for i, line_info in enumerate(new_pdf_info2):
		page_number = line_info["page_number"]
		if page_number not in page_info_dict.keys():
			page_info_dict[page_number] = {"text": ""}
		line_text = line_info["text"]
		if line_info["type"] == "table":
			markdoewn_table = table_to_markdown(line_text)
			page_info_dict[page_number]["text"] += markdoewn_table if page_info_dict[page_number][
				                                                          "text"] == "" else "\n" + markdoewn_table
		elif line_info["type"] == "directory":
			page_info_dict[page_number]["text"] += line_text if page_info_dict[page_number][
				                                                    "text"] == "" else "\n" + line_text
		elif line_info["type"] == "title":
			page_info_dict[page_number]["text"] += line_text if page_info_dict[page_number][
				                                                    "text"] == "" else "\n" + line_text
		elif line_info["type"] == "text":
			if line_info["text_flag"] == 1:
				page_info_dict[page_number]["text"] += line_text if page_info_dict[page_number][
					                                                    "text"] == "" else "\n" + line_text
			elif line_info["text_flag"] == 2:
				if page_info_dict[page_number]["text"] == "":
					if page_number - 1 in page_info_dict:
						page_info_dict[page_number - 1]["text"] += line_text
					else:
						page_info_dict[page_number]["text"] += line_text
				else:
					page_info_dict[page_number]["text"] += line_text
			elif line_info["text_flag"] == 3:
				if page_info_dict[page_number]["text"] == "":
					if page_number - 1 in page_info_dict:
						page_info_dict[page_number - 1]["text"] += line_text
					else:
						page_info_dict[page_number]["text"] += line_text
				else:
					page_info_dict[page_number]["text"] += line_text
		elif line_info["type"] == "table name":
			page_info_dict[page_number]["text"] += line_text if page_info_dict[page_number][
				                                                    "text"] == "" else "\n" + line_text
		elif line_info["type"] == "image name":
			page_info_dict[page_number]["text"] += line_text if page_info_dict[page_number][
				                                                    "text"] == "" else "\n" + line_text
		elif line_info["type"] == "clutter":
			page_info_dict[page_number]["text"] += line_text if page_info_dict[page_number][
				                                                    "text"] == "" else "\n" + line_text
		else:
			print(line_info)
	return page_info_dict

In [16]:
page_info_dict = get_page_info_dict(new_pdf_info2)

In [17]:
page_info_dict

{1: {'text': '韵达控股股份有限公司 \n2020 年年度报告 \n2021 年 04 月 '},
 2: {'text': '第一节 重要提示、目录和释义 \n公司董事会、监事会及董事、监事、高级管理人员保证年度报告内容的真实、准确、完整，不存在虚假记载、误导性陈述或重大遗漏，并承担个别和连带的法律责任。 \n公司负责人聂腾云、主管会计工作负责人谢万涛及会计机构负责人(会计主管人员)刘辉声明：保证本年度报告中财务报告的真实、准确、完整。 \n所有董事均已出席了审议本报告的董事会会议。 \n本报告中涉及的未来发展规划及经营目标相关的前瞻性陈述，属于计划性事项，不构成公司对投资者的实质承诺，敬请投资者理性投资，注意投资风险。 \n公司需遵守《深圳证券交易所行业信息披露指引第 9 号—上市公司从事快递服务业务》的披露要求。 \n公司在本年度报告中详细阐述了未来可能发生的有关风险因素及对策，详见“第四节经营情况讨论与分析”之“九、公司未来发展的展望”中的“可能面临的风险及应对措施”，敬请投资者予以关注。 \n公司经本次董事会审议通过的利润分配预案为：以利润分配实施时股权登记日的公司总股本为基数，向全体股东每 10 股派发现金红利 0.49 元（含税），送红股 0 股（含税），不以公积金转增股本。 '},
 3: {'text': '目录 \n第一节 重要提示、目录和释义 ..................................................................................................................... 2 \n第二节 公司简介和主要财务指标 ................................................................................................................. 5 \n第三节 公司业务概要 ..................................................................................................................................... 9

In [18]:
text = ""
for page_number,page_text in page_info_dict.items():
    text += "\n" +page_text['text']
print(text)


韵达控股股份有限公司 
2020 年年度报告 
2021 年 04 月 
第一节 重要提示、目录和释义 
公司董事会、监事会及董事、监事、高级管理人员保证年度报告内容的真实、准确、完整，不存在虚假记载、误导性陈述或重大遗漏，并承担个别和连带的法律责任。 
公司负责人聂腾云、主管会计工作负责人谢万涛及会计机构负责人(会计主管人员)刘辉声明：保证本年度报告中财务报告的真实、准确、完整。 
所有董事均已出席了审议本报告的董事会会议。 
本报告中涉及的未来发展规划及经营目标相关的前瞻性陈述，属于计划性事项，不构成公司对投资者的实质承诺，敬请投资者理性投资，注意投资风险。 
公司需遵守《深圳证券交易所行业信息披露指引第 9 号—上市公司从事快递服务业务》的披露要求。 
公司在本年度报告中详细阐述了未来可能发生的有关风险因素及对策，详见“第四节经营情况讨论与分析”之“九、公司未来发展的展望”中的“可能面临的风险及应对措施”，敬请投资者予以关注。 
公司经本次董事会审议通过的利润分配预案为：以利润分配实施时股权登记日的公司总股本为基数，向全体股东每 10 股派发现金红利 0.49 元（含税），送红股 0 股（含税），不以公积金转增股本。 
目录 
第一节 重要提示、目录和释义 ..................................................................................................................... 2 
第二节 公司简介和主要财务指标 ................................................................................................................. 5 
第三节 公司业务概要 ..................................................................................................................................... 9 
第四节 经营情况讨论与分析 ...........................................

In [19]:
import json
import requests

def chat_glm(prompt,temperature=0.01):
	headers: dict = {"Content-Type": "application/json"}
	url = "http://10.5.171.164:8002"
	response = requests.post(
		url=url,
		data=json.dumps(
			{"prompt": prompt, "max_length": 8000, "history": [], "temperature": temperature}
		),
		headers=headers,
	)
	res = response.json()
	result = res["response"]
	return result

In [28]:
a = '''
| 主要资产 | 重大变化说明 |
|---|---|
| 股权资产 | 本期无重大变化 |
| 固定资产 | 主要系报告期内房屋及建筑物、车辆、机器设备资产增加所致 |
| 无形资产 | 主要系报告期内购买计算机软件、土地所致 |
|  | 主要系黑龙江、山东、湖北、江苏等快递电商总部基地项目、韵达集团北方区域总 |
| 在建工程 | None |
| None | 部物流建设项目等增加所致 |
| 货币资金 | 主要系报告期内短期借款、应付债券增加，收回交易性金融资产所致 |
| 其他应收款 | 主要系报告期内备用金、押金及保证金增加所致 |
| 存货 | 主要系报告期内购买环保袋等周转材料增加所致 |
| 其他流动资产 | 主要系报告期内预缴增值税、企业所得税等增加所致 |
|  | 主要系报告期内可抵扣亏损、资产减值准备、递延收益、外汇货币工具公允价值变 |
| 递延所得税资产 | None |
| None | 动增加所致 |
| 其他非流动资产 | 主要系报告期内预付土地出让金、设备款、工程款增加所致 |'''

In [29]:
prompt_template = """
基于以下已知信息，简洁和专业的来回答用户的问题。
如果无法从中得到答案，请说 "根据已知信息无法回答该问题" 或 "没有提供足够的相关信息"，不允许在答案中添加编造成分，答案请使用中文。
已知内容:
{context}
问题:
{question}"""

In [30]:
prompt = prompt_template.format(context=a,question="固定资产的重大变化说明是什么？")
print(chat_glm(prompt))

固定资产的重大变化说明是：本期主要系报告期内房屋及建筑物、车辆、机器设备资产增加所致。


In [32]:
new_text = text[:6000]

In [163]:
prompt_template_question = """
请您根据下面的输入内容，提出三个中文问题，使用{'问题1':,'问题2':,'问题3':}的json格式输出。
输入内容：
"""

In [97]:
from pprint import pprint

In [94]:
prompt2 = prompt_template_question+ "\n" +new_text
return_dict = chat_glm(prompt2,temperature=0.85)

In [164]:
prompt2 = prompt_template_question + new_text[:2048]
for i in range(50):
    return_dict = chat_glm(prompt2,temperature=0.85).replace('\n','').replace('"',"'")
    if return_dict[0]!="{":
        return_dict = "{"+return_dict
    if return_dict[-1]!="}":
        return_dict = return_dict +"}"
    new_return_dict = return_dict[:-2].strip()
    if new_return_dict[-1]!="'":
        new_return_dict = new_return_dict +"'}"
    else:
        new_return_dict += "}"
    try:
        b = eval(new_return_dict)
        pprint(b)
        print('----'*40)
    except Exception as e:
        pprint(new_return_dict)
        print(e)
        print('----'*40)

{'问题1': '公司的利润分配预案是什么？', '问题2': '公司在哪些方面表达了前瞻性陈述？', '问题3': '公司是否需要遵守特定的披露要求？'}
----------------------------------------------------------------------------------------------------------------------------------------------------------------
{'问题1': '公司的基本面是什么？',
 '问题2': '公司在2020年和2021年的业绩如何？',
 '问题3': '公司在未来的发展中可能会遇到哪些风险和挑战？'}
----------------------------------------------------------------------------------------------------------------------------------------------------------------
{'问题1': '公司的利润分配预案是什么？', '问题2': '公司在哪些方面受到了监管？', '问题3': '公司的未来发展方向有哪些？'}
----------------------------------------------------------------------------------------------------------------------------------------------------------------
{'问题1': '公司的年度报告是在哪一年发布的？',
 '问题2': '公司的 board of directors 和 board of supervisors are responsible for '
        'ensuring the authenticity, accuracy and completeness of what aspect '
        'of the annual report?',
 '问题3': '在公司的这份年度报告中，关于未来发展规划和经营目标的前瞻性陈述是否构成了公司对投资者的实质承诺？'}


In [89]:
prompt_template_summary = """
我将给你输入一个PDF文件的文本内容，你需要对该文件的内容进行简单总结，100字以内。
PDF内容：
"""
prompt3 = prompt_template_summary+ "\n" +new_text
print(chat_glm(prompt3,temperature=0.35))

该 PDF 文件是韵达控股股份有限公司 2020 年年度报告。该公司是主要从事快递服务的公司，并在 report 中介绍了其经营情况、财务状况以及未来的发展计划。在经营情况方面，公司实现营业收入 335 亿元，同比下降 2.63%；净利润 140 亿元，同比下降 46.94%。在财务状况方面，公司总资产为 2950 亿元，归属于上市公司股东的净资产为 1438 亿元。在未来发展中，公司将继续优化网络布局、提升服务质量、扩大市场占有率，努力提高盈利水平。此外，公司还提到了需要遵守的相关法规和政策，以及可能面临的风险因素和应对措施。


In [165]:
t = '{\n  "问题1": "公司的 board of directors, audit committee, and independent directors are how many?",\n  "问题2": "the company\'s revenue growth rate in 2020 was what?",\n  "问题3": "which part of the annual report is related to the company\'s future development plans and business goals?"\n}'
t = t.replace("\n","").replace('"',"'")
print(t[-2])
if t[0]!="{":
    t = "{"+t
if t[-1]!="}":
    t = t +"}"
new_t = t[:-2].strip()
if new_t[-1]!="'":
    new_t = new_t +"'}"
else:
    new_t += "}"
print(new_t)
eval(new_t)

'
{  '问题1': '公司的 board of directors, audit committee, and independent directors are how many?',  '问题2': 'the company's revenue growth rate in 2020 was what?',  '问题3': 'which part of the annual report is related to the company's future development plans and business goals?'}


SyntaxError: invalid syntax. Perhaps you forgot a comma? (<string>, line 1)